### 9.1.1 语言模型简介
把句子看成单词的序列，语言模型可以表示为一个计算的模型。
 生成自然语言文本的应用依赖语言模型来优化输出文本的流畅性。
Seq2Seq模型可以看做是一个条件语言模型(Condational Language Model)
一个句子可以看作成一个单词序列：
                                                           
m为句子的长度，那么它的概率可以表示为
表示已知前m-1个单词时，第m个单词为的条件概率。

假设一门语言的词汇量为V，将的所有参数保存在一个模型里，需要个参数，为了顾及这些参数的取值，常见的方法有模型、决策树、最大熵模型、条件随机场、神经网络模型等。这里先用n-gram作为介绍，n-gram模型做出了一个有限历史假设：当前单词的出现概率仅仅与前面的n-1个单词相关，因此以上公式可以近似为：

                                                        

n指的是当前单词的个数。n-gram模型的参数一般采用最大似然估计(Maximum Likelihood Estimation, MLE)方法计算：
                                                        

C(X)表示单词序列X在训练语料中出现的次数。



### 9.1.2 语言模型的评价方法
语言模型效果好坏常用的复杂度(perplexity)。
                                                     

perplexity实际是计算每一个单词得到的概率倒数的几何平均，可以理解为平均分支系数(average branching factor)，即是模型预测下一个词时的平均可选择数量。

目前在PTB(Penn Tree Bank)数据集上最好的模型的perplexity为47.7。
通常来说采用perplexity的对数表达形式：

                                                   

在数学上， log perplexity可以堪称是真实分布和预测分布之间的交叉熵。假设x是一个离散变量，u(x)和v(x)诗两个与x香港的概率分布，那么u和v时间的交叉熵定义是分布u下-log(v(x))的期望值：
                                                 

把x看作单词，u(x)为每个位置上的真实分布，v(x)的模型的预测分布。

在给定上文条件下，语料中出现单词的概率为1，出现其他单词概率均为0。

In [1]:
import tensorflow as tf
# 假设词汇表的大小为3，语料包含两个单词“2 0”
word_labels = tf.constant([2, 0])

# 假设模型对两个单词预测时，产生的logit分别是[2.0, -1.0, 3.0]和[1.0, 0.0, -0.5]
# 注意这里的logit不是概率，因此它们不是0.0-1.0范围之间的数字。
# 则需要调用prob=tf.nn.softmax(logits)。但这里计算交叉熵的函数直接输入logits
predict_logits = tf.constant([[2.0, -1.0, 3.0], [1.0, 0.0, -0.5]])

# 使用sparse_softmax_cross_entropy_with_logits计算交叉熵。
loss = tf.nn.sparse_softmax_cross_entropy_with_logits(
    labels = word_labels, logits= predict_logits)

# 运行程序，计算loss的结果
sess = tf.Session()
sess.run(loss)

# sparse_softmax_cross_entropy_with_logits与上面函数相似
word_prob_distribution = tf.constant([[0.0, 0.0, 1.0], [1.0, 0.0, 0.0]])
loss = tf.nn.softmax_cross_entropy_with_logits(
    labels = word_prob_distribution, logits = predict_logits)
# 运行结果
sess.run(loss)

# 由于sparse_softmax_cross_entropy_with_logits允许提供一个概率分布，一种叫label_smoothing的技巧是将正确数据的概率设比为一个比1.0略高的值
word_prob_smooth = tf.constant([[0.01, 0.01, 0.98], [0.98, 0.01, 0.01]])
loss = tf.nn.softmax_cross_entropy_with_logits(
    labels = word_prob_smooth, logits = predict_logits)

sess.run(loss)

array([0.37656265, 0.48936883], dtype=float32)

## 9.2 神经语言模型
使用循环神经网络，对每个时刻输入·为句子的单词，而每个时刻的输出为一个概率分布。

### 9.2.1 PTB数据集的预处理
在网站上下载PTB数据，为了将文本转换为模型可以读入的单词序列，先将10000个词汇分别映射到0-9999之间的整数编号。
下面的辅助程序首先按照词频顺序为每个词汇分配一个编号，然后将词汇表保存到一个vocab文件中。



In [1]:
import codecs
import collections
from operator import itemgetter

RAW_DATA = "C:/Users/adward/Desktop/TensorFlow-Google/simple-examples/data/ptb.train.txt"
VOCAB_OUTPUT = 'ptb.vocab'            # 输出词汇表文件

counter = collections.Counter()       # 统计单词出现频率count
with codecs.open(RAW_DATA, "r", "utf-8") as f:  # 每一行读取
    for line in f:
        for word in line.strip().split():       # 切割分词
            counter[word] += 1

# 按照词频顺序对单词排序
sorted_word_to_cnt = sorted(counter.items(),
                           key = itemgetter(1),
                           reverse = True)
sorted_words = [x[0] for x in sorted_word_to_cnt]

# 在文本换行处加上句子结束符<eos>，预先加入词汇表
sorted_words = ["<eos>"] + sorted_words

'''
除了<eos>还需要将低频<unk>和句子起始符<sos>加入词汇表，并且删除低频词汇，因为在PTB数据中已经替换了低频词汇，所以不需要这一步
sorted_words = ["<unk>","<sos>","<eos>"] + sorted_words
if len(sorted_words)>10000:
sorted_words = sorted_words[:10000]
'''
with codecs.open(VOCAB_OUTPUT, 'w', 'utf-8') as file_output:
    for word in sorted_words:
        file_output.write(word + "\n")
    print("success")

success


In [2]:
import codecs
import sys

RAW_DATA = "C:/Users/adward/Desktop/TensorFlow-Google/simple-examples/data/ptb.train.txt"
VOCAB = "ptb.vocab"                # 上面生成的词汇表文件
OUTPUT_DATA = "ptb.train"                 # 将单词替换问单词编号后的输出文件

# 读取词汇表，并建立词汇到单词编号的映射
with codecs.open(VOCAB, 'r', 'utf-8') as f_vocab:
    vocab = [w.strip() for w in f_vocab.readlines()]
word_to_id = {k: v for (k, v) in zip(vocab, range(len(vocab)))}

# 如果发现了被删除的低频词，则替换为"<unk>
def get_id(word):
    return word_to_id[word] if word in word_to_id else word_to_id["<unk>"]

fin = codecs.open(RAW_DATA, "r", "utf-8")
fout = codecs.open(OUTPUT_DATA, "w", "utf-8")
for line in fin: 
    words = line.strip().split() + ["<eos>"] # 读取单词并添加<eos>结束符
    # 将每个单词替换为词汇表的编号
    out_line = ' '.join([str(get_id(w)) for w in words]) + '\n'
    fout.write(out_line)
    #print(out_line)
fin.close()
fout.close()

In [6]:
with codecs.open(VOCAB, 'r', 'utf-8') as f_vocab:
    #vocab = [w.strip() for w in f_vocab.readlines()]
    #print(vocab)
    for w in f_vocab.readlines():
        print(w.strip())

<eos>
the
<unk>
N
of
to
a
in
and
's
that
for
$
is
it
said
on
by
at
as
from
million
with
mr.
was
be
are
its
he
but
has
an
n't
will
have
new
or
company
they
this
year
which
would
about
says
more
were
market
billion
his
had
their
up
u.s.
one
than
who
some
been
also
stock
other
share
not
we
corp.
if
when
i
last
president
shares
years
all
first
two
because
trading
after
could
inc.
sales
&
there
out
business
only
do
such
can
most
into
york
may
over
co.
group
many
government
now
federal
companies
no
time
bank
so
any
cents
people
quarter
you
exchange
prices
even
what
price
investors
say
down
rose
while
much
yesterday
week
under
securities
months
them
bonds
big
next
interest
three
earlier
net
'
earnings
make
major
state
american
financial
chairman
did
these
investment
board
still
through
stocks
those
just
chief
industry
executive
since
program
before
rate
made
officials
money
national
she
analysts
house
like
unit
month
off
expected
days
rates
japanese
against
does
plan
profit
between
both
capit

connecticut
fill
suspension
newport
brain
plenty
deep
whites
plastics
solid
ideas
concrete
mobil
stadium
nevertheless
earn
poison
rebound
secret
coke
recommended
risen
watching
sustained
delivered
telling
monitor
miss
suffer
duties
wild
caution
abortions
helps
sex
productivity
fans
fundamental
host
drew
projections
marketplace
simmons
assumption
inquiry
indicating
onto
germans
cast
credits
assuming
amr
intense
dramatic
commonwealth
michigan
feeling
crowd
biotechnology
thomson
decades
experienced
subsidies
basket
cheap
sheet
killed
nomura
mcdonald
oppose
downward
criticized
imported
sit
christopher
younger
permission
cheaper
judicial
candidate
powers
timing
remic
webster
hahn
license
attempting
phoenix
difficulties
conservatives
complaints
eager
stood
underwriter
gov.
waertsilae
encouraged
cycle
charging
approximately
d.c.
copy
teachers
ride
driving
intent
steep
draw
selected
checks
author
wish
capped
slump
overnight
relative
dutch
interbank
vegas
referring
telegraph
requested
milk
flyi

unspecified
brazilian
boosts
voices
wilson
port
handed
genentech
accessories
circle
judiciary
disputed
lure
gaining
theft
gauge
intelogic
politburo
dictator
subsequently
affidavit
lie
deeper
hidden
pressed
excellent
disobedience
peck
shed
farms
destroy
pinnacle
administrator
statute
targeting
s
stoll
supervision
funny
advantages
norton
sydney
creek
mistake
throwing
reward
provider
freeman
tuition
sessions
capable
homeowners
anticipates
mtm
territory
discovery
influenced
interpreted
lows
victor
slipping
tissue
lucky
acceptances
dated
doubling
lights
elizabeth
academy
gambling
questioned
weaken
watson
aims
tenure
illuminating
max
retiring
spots
withdrawn
frequent
proportion
equity-purchase
hampered
oversees
pregnancy
issuers
fought
interpretation
surfaced
quotes
rican
destruction
inco
postal
springs
evident
rigid
jay
conversation
steelmaker
establishing
slated
deductions
stalled
cabrera
instructions
issuing
austin
microsystems
scared
dump
recording
donated
bruce
300-a-share
protecting
st

beings
vermont-slauson
relax
accurately
capitalized
venezuela
polyethylene
overcapacity
hubbard
packed
stereo
liberals
intensity
coin
chores
clash
implement
'80s
stern
daf
incorporated
suspected
earthquake-related
layoffs
inspector
ems
arbitrator
unpopular
barclays
meaningful
clues
angered
unwilling
struggled
hurdles
pale
pumped
mushrooms
vague
backup
murdered
chevy
mercedes
pork-barrel
cnw
aquino
bergsma
restraint
simon
palm
wilbur
exotic
effectiveness
thornburgh
seniority
across-the-board
walked
soliciting
energetic
applicants
suez
guns
volumes
utsumi
disabilities
joint-venture
third-largest
portrayal
novels
bikers
wyoming
wholly
fantasy
unix
woolworth
capitalist
trailed
fazio
economically
merits
installation
pizza
commenting
sovereignty
ratios
pitches
determination
disabled
deserves
titled
phrase
titles
convex
s.c
flowing
unification
searle
mcalpine
unesco
memphis
ambitions
raiders
disappear
pawn
inspection
weekes
urges
toxic
punishment
delaying
prize
jazz
shakespeare
demonstrate
tw

wellcome
remark
masters
taping
fernandez
vault
integrate
someday
resembles
reoffered
pierre
cilcorp
abused
laundering
name-dropping
watts
birthday
gatward
sink
inaccurate
picket
brunt
gutfreund
pickens
ratified
intervened
ian
extraordinarily
listings
boone
reupke
patch
reinforcing
pits
allowance
domination
switches
prerogatives
sights
whichever
loath
multibillion-dollar
confirming
boesel
thoroughbred
bologna
brown-forman
foreclosed
loser
ig
tampa
forum
resemble
contemplated
liquidate
theoretical
adversary
teagan
thailand
dodd
two-tier
fasteners
jeans
supermarkets
redemptions
gubernatorial
flush
ifi
folk
terminate
carolinas
notable
edgar
rafale
fdic
designers
protocol
sherman
medication
parkway
shirts
traveled
cry
dlj
upgrading
blessing
itel
minimum-wage
bunch
coordinator
prefers
explosive
neat
memorandum
firstsouth
modified
dai-ichi
viability
halloween
fool
downey
posner
carry-forward
l.p.
fatal
\*\*
crusade
hazard
gallons
ncaa
petco
reins
brains
bloated
shots
aba
heaviest
creeping
exa

In [7]:
word_to_id

{'h.': 2158,
 'poll': 2765,
 'strategic': 1749,
 'andreas': 8569,
 'exemption': 6277,
 'disruptions': 7825,
 'transit': 6944,
 'investment': 145,
 'wildlife': 6720,
 'teddy': 4407,
 'sounds': 3919,
 'owning': 3920,
 'public': 273,
 'retreat': 5882,
 'reimburse': 9783,
 'standstill': 6721,
 'tainted': 9249,
 'dismiss': 7826,
 'dunkin': 8403,
 'decisions': 1838,
 'airline': 763,
 'pulp': 2518,
 'belli': 7827,
 'newspaper': 1139,
 'replacing': 5051,
 'vivid': 9859,
 'drop': 468,
 'consider': 928,
 'analysts': 164,
 'convey': 9583,
 'portfolio': 678,
 'loans': 360,
 'announcer': 6035,
 'marathon': 6279,
 'circumstances': 2287,
 'fierce': 6602,
 'homer': 7829,
 'hostile': 1776,
 'term': 1077,
 'breaker': 6794,
 'willful': 9956,
 'somewhat': 2707,
 'such': 88,
 'arrive': 5884,
 'hanover': 2519,
 'benton': 9584,
 'task': 1993,
 'would': 42,
 'riding': 5885,
 'regulatory': 1377,
 'situation': 941,
 'mimic': 9860,
 'ability': 1140,
 'wertheim': 7314,
 'examiner': 5788,
 'bellwether': 6491,
 'th

In [8]:
word_to_id['much']

121

In [9]:
fin = codecs.open(RAW_DATA, "r", "utf-8")
fout = codecs.open(OUTPUT_DATA, "w", "utf-8")
for line in fin: 
    words = line.strip().split() + ["<eos>"] # 读取单词并添加<eos>结束符
    # 将每个单词替换为词汇表的编号
    out_line = ' '.join([str(get_id(w)) for w in words]) + '\n'
    print(out_line)

9977 9989 9992 9999 9996 9990 9987 9976 9984 9988 9981 9972 9978 9982 9970 9971 9975 9974 9986 9993 9979 9985 9994 9973 0

9450 2 3 72 394 33 2133 1 146 19 6 8979 276 408 3 0

23 2 13 142 4 2 5553 1 3065 1594 96 0

7767 2 3 72 394 8 337 142 4 2509 662 2173 954 24 521 6 8979 276 4 39 303 437 3690 0

6 946 4 3160 495 262 5 137 6003 4317 5915 30 992 6 241 756 4 1016 2791 211 6 96 4 429 4169 5 14 45 55 3 72 195 1246 220 0

1 3160 7270 2 13 3966 2 495 14 6935 1 2 22 113 2685 8126 5 14 2469 5241 10 462 52 3009 467 1246 15 0

2 80 1 167 4 35 2630 2 65 10 557 6003 3621 1890 664 2 7 27 2 4317 5915 7 3 0

367 1976 3223 46 220 45 55 6 40 195 1 465 342 1301 7 325 9 35 1499 920 4 3147 6 9491 371 5 1147 35 1412 5 1 432 0

6 2 2 15 39 13 31 394 1365 0

64 277 1915 43 72 195 157 1449 2416 4 3160 717 106 5624 1303 0

83 13 102 3160 7 227 189 99 0

1408 2 1409 1 1246 56 4340 1 429 46 2656 4 106 322 16 8400 4 1 6003 3621 0

64 34 102 4141 531 16 368 2332 26 18 646 15 560 944 2 4 651 9 2 1016 758 0

977 2

144 1336 93 63 3558 25 124 1338 67 38 3455 690 0

23 2 15 83 59 93 25 61 2287 124 41 1336 42 32 358 1 98 5 478 38 50 3769 1462 534 690 0

4794 84 3074 2745 43 144 1336 42 6653 1 1052 169 8 5488 587 174 1 766 28 15 0

1 534 690 135 96 2275 6 1993 535 39 123 2 17 35 92 753 4129 2 5 497 22 1 1201 0

1 140 2752 441 9 165 4 9719 1356 6 2054 7 3 2 1 1052 2176 4921 0

799 2163 6 35 92 1360 56 2538 1 9555 9 1438 1369 374 15 10 690 26 5940 17 1 9555 9 2382 4 4773 20 9734 531 43 6 1790 1608 251 6 212 454 14 36 5 1388 1 1790 20 9767 6 1462 761 10 79 410 7 1236 0

23 2163 15 28 1312 22 160 4 1 1052 8 1 1005 236 41 42 1147 106 2561 1609 174 2199 5 2143 1 185 69 93 0

18 10 473 28 15 1 1005 236 5246 299 10 2561 2717 42 32 25 2560 174 1848 349 392 1274 8 1639 4212 0

23 2163 15 1052 160 1793 1 1005 236 9 2462 3908 16 1 1201 0

29 7 1 2197 1003 7 181 171 3023 892 2 4 1 1052 4173 723 7 2937 550 1848 10 3403 5 6076 4371 1 3070 531 79 410 7 2 2561 587 213 6826 0

7 57 679 1 1052 613 11 531 9100 192 5 274


23 2 1389 18 479 11 3 72 476 6 2817 4 601 8 2 1371 0

1 2311 5 652 2 6831 205 2 39 123 67 1 1151 212 2055 5 2559 31 1693 20 6 307 10 44 353 1813 404 254 2076 113 78 5435 10 38 79 63 2399 34 992 1 5403 0

64 89 2219 8 62 1 2 10 557 1869 1273 3060 5 208 6 943 4 2 872 5 150 56 575 58 1012 0

29 39 307 13 6 7612 5307 7 242 1 3569 4 1 1504 2 793 34 695 1 1937 19 1 86 9491 39 357 30 5 1563 646 502 8 5974 0

306 516 99 6 1129 212 528 2908 1 6360 11 61 245 9115 679 0

20 1 2 314 3 57 75 21 938 450 1 6173 2 2 2743 5 1388 2 8 1204 2 0

1 509 24 682 17 1 622 8 509 343 8 5522 17 57 3 1933 101 516 124 7768 6479 0

7 1 2215 1478 220 1016 679 211 1 5694 4 2743 2332 0

1 679 912 788 5 212 29 1 7368 4 248 4060 2743 3552 79 32 4719 624 1082 38 262 0

934 7 3 1937 7 248 598 210 296 8 35 92 1102 5 6698 1 2 1167 10 3552 404 2000 10 1 1813 26 1 1454 56 26 5586 0

1937 159 1 2992 10 73 2743 4841 46 2642 1 312 8 1048 6 9763 898 105 10 2076 42 25 9005 174 509 765 7 1 5164 4 51 62 4 1 1533 81 0

39 30 57 4893 


1586 7 31 3155 305 16 1 1438 1369 9 237 1348 10 18 1180 422 155 3 28 1014 6 2967 8 2157 131 7 6 2356 2 2 5106 1447 774 7 308 459 10 3164 31 1597 4101 4 131 388 52 6 2 2268 5 184 6 601 8 2134 239 11 49 337 8099 99 49 334 1969 8 3225 3 908 7 363 249 7 6211 1230 0

7 3620 2500 7 1 1438 1369 237 212 457 15 1 401 99 3 72 394 2 49 8702 159 3285 2693 16 49 857 8 2 1449 56 8211 299 0

2 2603 38 46 970 5 2 299 5 8 20 221 2 49 5952 2 49 3097 7740 49 601 8 113 468 17 49 165 5 4792 49 75 2373 2 2 8 2 0

54 337 2 1667 10 1 401 2 299 17 2 16 6 2036 4 6 500 1124 786 78 2 6 12 3 6097 0

57 4 1 2470 26 948 9689 0

75 337 8702 550 1 1438 1369 38 46 7616 5 1 401 9 7184 16 1125 6403 5 209 2 86 5 676 1 401 7 49 2 7569 0

54 716 6634 10 1 401 495 341 199 5 49 283 120 4607 1024 18 73 0

1 401 1940 20 49 4078 1486 49 1168 41 542 39 123 2 4243 73 1 2470 174 299 2379 127 2 8 2 389 2 0

28 6667 1 3155 16 576 389 2 2 22 49 2217 701 5 728 1 8189 9 2 8 6 2 17 139 3992 8 1586 7472 17 57 4 49 9366 174 127 0

68 87 3


29 83 26 1682 10 3178 2331 79 427 1 2105 4 2235 804 8 1 2819 4 3147 0

68 564 32 3316 6 103 67 1770 1382 89 1849 16 114 1 432 13 44 23 3319 56 2538 1 2 9 236 2566 22 466 2110 0

76 1 256 343 13 32 832 1 2820 16 466 250 85 493 26 2566 22 913 1155 56 4536 2235 7847 0

85 1175 1 357 13 506 45 103 6745 39 185 44 968 2111 3081 673 2695 0

14 9 6 2 185 0

85 2524 133 39 40 67 968 3081 1196 6 260 10 42 1208 2434 5 578 6 1079 461 4 466 239 5 429 29 175 32 3889 2 1316 0

1110 7 1114 6 6168 96 4 1991 20 1 571 8 700 3297 13 2 6 176 5 2237 2788 414 0

14 33 4593 6 2 1205 1098 5 585 2453 990 20 8560 206 856 112 0

18 3 3 4 2002 162 518 53 466 270 292 26 1 1590 7 1 219 0

17 1931 202 9 1934 3 3 4 3260 6 508 9 344 1458 4 807 8 323 0

265 8 700 1999 10 1 2471 557 53 101 245 1649 0

1980 65 780 10 466 270 1217 12 3 5 1 115 4 214 4 27 699 43 12 3 5 12 3 45 1037 601 55 244 1411 254 11 466 0

1 362 4 466 856 13 8832 1406 4 2027 8 2 437 1523 5349 2458 2 6 1980 2 2567 0

700 13 4195 76 97 101 26 664 206 16

...

1 146 15 1 1460 3870 42 25 897 16 1 2151 10 740 774 42 59 25 1153 5 257 11 1 5770 2804 537 16 519 709 5 150 492 5 53 527 0

53 848 34 292 58 7285 52 0

38 533 9782 65 483 734 65 686 1950 7275 95 8 3431 537 2362 572 0

1 806 79 410 7 1 53 832 45 55 3 3 4 27 1008 537 1781 20 725 52 20 43 3 3 488 0

14 42 1147 3 537 2173 91 359 18 6 1564 158 4 43 3 48 4692 1342 6 272 0

1 146 451 10 1 362 4 484 6 2362 20 1 5770 2804 5 5574 42 25 43 1516 3 21 0

14 59 15 2989 4 9222 53 436 11 1008 537 8 115 2296 4 1516 3 1037 4060 4692 1342 17 3 42 137 1 806 7519 5487 0

9043 6 167 4 3285 268 554 41 13 2 17 1675 65 33 25 1153 5 1460 3 1735 4692 1342 5 1 53 7 1 6931 340 0

2934 6 657 4 2739 2 96 33 25 1153 5 1460 3 1735 4692 1342 8 1480 6 167 4 6896 82 92 3139 554 33 25 1153 5 1460 3 1735 4692 1342 0

6577 1308 80 4067 2053 15 14 238 8 345 5 183 248 745 8 2 434 11 43 12 3 21 41 33 25 262 11 2316 207 8 187 2890 0

1 1084 26 5024 0

1 37 345 5 183 27 1407 745 7 765 4 2 8 864 548 3578 2 8 2 82 2 5 1 138 1025 7

28 44 1 2925 4 9579 679 1573 189 10 93 34 262 2823 2772 17 31 2618 2206 4548 20 6 1636 5 7373 8328 1 189 0

29 28 44 10 9 102 45 6 879 11 4512 2618 2 55 884 4365 26 6 879 11 4512 699 0

3124 87 32 184 88 3941 0

1227 2171 213 114 14 13 108 87 32 850 2007 5189 44 1728 2 152 4 622 957 11 1 35 92 139 466 236 0

809 1 6329 174 1 2618 2206 30 58 558 2618 855 0

1 2 6708 218 96 30 897 6 8807 1285 10 596 1 1046 13 6 466 9547 8 10 23 3133 13 546 5 137 6 2507 6345 18 1 2452 4 1 508 9 2618 855 0

1 2 1251 5 472 29 1 96 9 753 4770 2 44 1 96 9 1609 26 9342 4964 17 466 829 0

31 266 2 24 1 53 236 4 2764 0

23 3133 2090 1072 726 11 49 1046 5 25 262 18 2 1192 5509 17 1 2 9 622 1263 7545 336 0

3688 11 23 3133 205 2162 4 1 2 1 4051 608 336 24 7 526 4 2823 0

78 3564 3039 20 2618 855 39 2162 595 1 61 2162 5 2 27 726 1108 5386 1 1046 9 647 47 5 2 8 2712 8 61 2 10 26 32 5509 17 1 2 0

1 2618 855 59 9801 1 622 8 509 343 0

29 1 3308 7 6 3 1109 5 1 558 2618 855 15 10 83 24 326 5673 4 6 466 432 19 350 19 51


120 1 2 143 34 350 2494 7654 1120 2 148 127 11 7678 38 1078 6001 31 3560 294 4 2494 2218 10 611 2 148 1 4500 15 7860 4800 6 1997 5638 7 641 749 0

7207 325 1843 6 2 4 1 1505 23 4800 4723 22 2 602 2 2234 0

29 7 1 307 4 1 7623 3073 1 1436 4 88 414 992 1 1863 4 1 4086 5 2 8 9021 124 1 3392 4 1 334 7813 2 2 56 46 7285 52 7 2 2 1707 16 1 230 7813 440 3 1342 628 0

160 4 1 139 302 143 32 34 106 1938 4150 762 1 7678 143 32 837 52 0

7207 8510 1 1853 7 3 19 201 4 6 12 3 21 8330 806 664 602 2 5 6811 1 2 4 1 3073 5 1 4086 8 1388 1 1750 20 2 7 6 1062 0

7207 300 2773 2 7 3837 411 5 2879 1 1308 191 10 143 1 7678 221 0

1755 7 1 1475 8 2080 2 33 2 387 368 98 450 2862 856 5 838 8 1348 1 3588 44 400 2 6 2 6296 8132 753 56 4663 7 1853 1505 8 2565 679 0

1 191 1131 7 5 4347 1 1750 79 25 5586 19 200 0

1 342 4 1 1062 1526 630 1085 43 368 2862 856 24 639 23 2 44 0

730 1 8623 966 4 1 760 448 14 901 5 808 10 6 3 426 13 6 9568 1930 0

7207 135 23 2 5223 1 302 9 221 16 1 7623 3073 0

1 221 24 927 4271 28 


6 206 5164 4 752 945 4459 55 442 945 0

120 440 1934 2 4 752 8 442 938 488 4459 7 179 2 45 2956 34 730 52 3670 55 1895 0

7 2 511 7 4329 172 94 1 224 1223 1 2 935 2824 86 18 1895 8 2956 0

2 8 5230 1018 46 32 4340 8446 46 648 22 2956 0

181 511 7 197 366 2 7579 172 1037 3 2475 17 2487 8 2983 0

442 6700 0

442 2 0

752 6700 0

752 2 0

750 1241 1174 4740 2 488 231 2 931 1936 5 638 1 37 9 513 3049 283 0

19 231 2 1552 23 2 33 221 22 2213 9 524 265 8 22 1 37 9 2 857 5 2011 2213 9 774 18 1 100 461 15 400 3088 2 142 8 152 154 290 0

23 2 15 1 3665 8614 1 775 1922 4 98 16 227 85 0

23 2 3 72 394 30 58 22 1 129 1598 4 2251 189 622 8 3526 11 3 72 0

279 546 5 177 20 1 181 932 7 141 190 2 1 1347 1234 47 5471 113 45 2039 7 60 112 0

78 5096 1523 198 6 2685 2 67 77 542 1 1347 430 216 4725 124 399 839 0

1 1259 18 221 648 5934 77 19 200 19 2 47 765 8 1256 116 56 50 683 60 16 1 3013 198 1 181 6966 0

198 1 69 75 890 4 77 1 430 514 2988 113 16 1 272 157 5143 555 0

1 1347 430 247 118 3 36 3 3 5 3 

1 565 4171 12 3 48 4 1361 3704 2059 475 1 334 3704 331 7 75 171 0

1 330 41 2 180 91 1 274 13 917 19 31 677 5 2 1 2 190 10 1 53 876 104 13 1801 5 578 1 7005 1862 0

29 61 164 3299 10 120 1 565 9 330 5 8119 355 30 32 58 2217 14 2963 6904 6 728 2406 10 18 297 11 99 1 565 30 2 27 5310 16 355 0

38 1217 10 1 565 30 1153 1 862 100 193 131 158 5 8712 5 43 3 3 3 20 27 792 4 151 628 3 3 69 123 0

1 100 193 158 13 1 3063 1718 158 10 249 526 214 61 0

47 2320 15 10 1 1063 1057 5 1100 1 90 889 553 174 1 332 0

16 1 1394 111 7 35 92 662 11 264 998 1614 18 12 3 31 1903 52 3 107 0

451 395 24 6 2462 3 21 3787 0

7 266 77 7 800 841 910 662 24 18 12 3 31 1903 0

162 2202 65 15 14 1614 6 8804 2072 9942 307 174 8881 502 65 17 5073 6 12 3 21 1210 20 8881 7 111 11 8496 8881 2 3870 11 73 189 836 0

1 75 101 59 345 5 1935 106 507 811 536 250 94 1 130 3 72 148 2 7986 179 101 15 0

1 189 26 1364 2 2250 7410 10 34 2573 7 1 580 1298 3096 8 1284 8939 190 0

8881 502 2 852 341 1 918 1784 155 189 2119 17 1 5094 46

In [10]:
fout = codecs.open("ptb.train", 'r', 'utf-8')
print(fout.readlines())

[]


### 9.2.2 PTB数据的batching方法
文本数据中，由于每个句子的长度不同，所以在进行batching时需要采取一些特殊操作。最常见是使用填充（padding）将同一个batch的句子长度补齐。

In [3]:
import tensorflow as tf
import numpy as np

TRAIN_DATA = "ptb.train"
TRAIN_BATCH_SIZE = 20
TRAIN_NUM_STEP = 35

# 从文件读取数据，并返回包含单词编号的数组
def read_data(file_path):
    with open(file_path, "r") as fin: 
        # 将整个文档读进一个长字符串
        id_string = ''.join([line.strip() for line in fin.readlines()])
    # 将读取的单词编号转为整数
    id_list = [int(w) for w in id_string.split()]
    return id_list

def make_batches(id_list, batch_size, num_step):
    # 计算总的batch数量。每一个batch包含的单词数量是batch_sieze * num_step
    num_batches = (len(id_list) - 1) // (batch_size * num_step)
    
    # 将数据整理成一个维度为[batch_size, num_batches * num_step]的二维数组
    data = np.array(id_list[: num_batches * batch_size * num_step])
    data = np.reshape(data, [batch_size, num_batches * num_step])
    # 沿着第二个维度将数据切分成num_batches个batch，存入一个数组
    data_batches = np.split(data, num_batches, axis = 1)
    
    # 重复上一个操作，这里得到的是RNN每一步输出所需要预测的下一个单词
    label = np.array(id_list[1 : num_batches * batch_size * num_step + 1])
    label = np.reshape(label, [batch_size, num_batches * num_step])
    label_batches = np.split(label, num_batches, axis = 1)
    
    # 返回一个长度为num_batches的数组，每一项包括一个data矩阵和一个label矩阵
    return list(zip(data_batches, label_batches))


def main():
    train_batches = make_batches(read_data(TRAIN_DATA), TRAIN_BATCH_SIZE, TRAIN_NUM_STEP)
    
if __name__ == "__main__":
    main()

In [4]:
with open("ptb.train", "r") as fin: 
    # 将整个文档读进一个长字符串
    id_string = ''.join([line.strip() for line in fin.readlines()])
# 将读取的单词编号转为整数
id_list = [int(w) for w in id_string.split()]
print(id_list)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


### 9.2.3 基于循环神经网络的神经语言模型
NLP应用中主要多了两个层： 词向量层(embedding)和softmax层

词向量层
将词汇表嵌入到一个固定维度的实数空间。主要有两大作用：

1. 降低输入的维度。如果不适用词向量而是以one-hot vector形式输入循环神经网络，那么输入的维度将和词汇量大小相同，通常在10000以上，而词向量维度在200-1000之间。
2. 增加语义信息。简单的单词编号不包含任何语义信息，词向量将稀疏的编号转化为稠密的向量。比如猫或者狗带来的影响可能是相似的，这样的模型下，猫和狗的词向量取值可能是相近的。


In [101]:
# 假设词向量维度是EMB_SIZE，词汇表大小为VOCAB_SIZE，那么所有单词可以放入大小为VOCAB_SIZE x EMB_SIZE的矩阵内。
embedding = tf.get_variable("embedding",[VOCAB_SIZE, EMB_SIZE])

# 输出的矩阵比输入的数据多一个维度，一般输入的大小是batch_size x num_steps，
# 而输出的input_embedding维度是batch_size x num_steps x EMB_SIZE
input_embedding = tf.nn.embedding_lookup(embedding, input_data)


NameError: name 'VOCAB_SIZE' is not defined

Softmax层——将循环神经网络的输出转化为一个单词表中每个单词的输出概率
使用一个线性映射将循环神经网络的输出映射为一个维度与词汇表大小相同的向量，这一步叫logits。

In [ ]:
# 定义线性映射用到的参数
# HIDDEN_SIZE是循环神经网络的隐藏状态维度，VOCAB_SIZE是词汇表大小
weight = tf.get_variable("embedding",[HIDDEN_SIZE, VOCAB_SIZE])
bias = tf.get_variabel("bias", [VOCAB_SIZE])

# 计算线性映射
# output是RNN的输出，其维度为[batch_size * num_steps, HIDDEN_SIZE]
logits = tf.nn.bias_add(tf.matmul(output, weight), bias)

调用Softmax方法将logits转化为和为1的概率

In [ ]:
# probs的维度与logits的维度相同
probs = tf.nn.softmax(logits)

模型不关心概率的具体取值，而更关心最终的log perplexity

In [ ]:
loss = tf.nn.sparse_softmax_cross_entropy_with_logits(
    labels = tf.reshape(self.targets, [-1]), logits = logits)


通过共享参数减少参数数量  
softmax层和词向量层都与词汇表大小 VOCAB_SIZE成正比，并且往往都很多。  

我们可以共享词向量层和Softmax层的参数，不仅可以大幅减少参数量，还能提高模型效果。

In [1]:
# coding: utf-8
import numpy as np
import tensorflow as tf



1.设置参数。

In [2]:
#TRAIN_PATH = "C:/Users/adward/Desktop/TensorFlow-Google/simple-examples/data/ptb.train.txt"          # 训练数据路径。
#EVAL_PATH = "C:/Users/adward/Desktop/TensorFlow-Google/simple-examples/data/ptb.valid.txt"           # 验证数据路径。
#TEST_PATH = "C:/Users/adward/Desktop/TensorFlow-Google/simple-examples/data/ptb.test.txt"            # 测试数据路径。

TRAIN_DATA = "ptb.train"          # 训练数据路径。
EVAL_DATA = "ptb.valid"           # 验证数据路径。
TEST_DATA = "ptb.test"            # 测试数据路径。
HIDDEN_SIZE = 300                 # 隐藏层规模。
NUM_LAYERS = 2                    # 深层循环神经网络中LSTM结构的层数。
VOCAB_SIZE = 10000                # 词典规模。
TRAIN_BATCH_SIZE = 20             # 训练数据batch的大小。
TRAIN_NUM_STEP = 35               # 训练数据截断长度。

EVAL_BATCH_SIZE = 1               # 测试数据batch的大小。
EVAL_NUM_STEP = 1                 # 测试数据截断长度。
NUM_EPOCH = 5                     # 使用训练数据的轮数。
LSTM_KEEP_PROB = 0.9              # LSTM节点不被dropout的概率。
EMBEDDING_KEEP_PROB = 0.9         # 词向量不被dropout的概率。
MAX_GRAD_NORM = 5                 # 用于控制梯度膨胀的梯度大小上限。
SHARE_EMB_AND_SOFTMAX = True      # 在Softmax层和词向量层之间共享参数。

2.定义模型。

In [3]:
# 通过一个PTBModel类来描述模型，这样方便维护循环神经网络中的状态。
class PTBModel(object):
    def __init__(self, is_training, batch_size, num_steps):
        # 记录使用的batch大小和截断长度。
        self.batch_size = batch_size
        self.num_steps = num_steps
        
        # 定义每一步的输入和预期输出。两者的维度都是[batch_size, num_steps]。
        self.input_data = tf.placeholder(tf.int32, [batch_size, num_steps])
        self.targets = tf.placeholder(tf.int32, [batch_size, num_steps])
        
        # 定义使用LSTM结构为循环体结构且使用dropout的深层循环神经网络。
        dropout_keep_prob = LSTM_KEEP_PROB if is_training else 1.0
        lstm_cells = [
            tf.nn.rnn_cell.DropoutWrapper(
                tf.nn.rnn_cell.BasicLSTMCell(HIDDEN_SIZE),
                output_keep_prob=dropout_keep_prob)
            for _ in range(NUM_LAYERS)]     
        cell = tf.nn.rnn_cell.MultiRNNCell(lstm_cells)            
        
        # 初始化最初的状态，即全零的向量。这个量只在每个epoch初始化第一个batch
        # 时使用。
        self.initial_state = cell.zero_state(batch_size, tf.float32)

        # 定义单词的词向量矩阵。
        embedding = tf.get_variable("embedding", [VOCAB_SIZE, HIDDEN_SIZE])
        
        # 将输入单词转化为词向量。
        inputs = tf.nn.embedding_lookup(embedding, self.input_data)
        
        # 只在训练时使用dropout。
        if is_training:
            inputs = tf.nn.dropout(inputs, EMBEDDING_KEEP_PROB)
 
        # 定义输出列表。在这里先将不同时刻LSTM结构的输出收集起来，再一起提供给
        # softmax层。
        outputs = []
        state = self.initial_state
        with tf.variable_scope("RNN"):
            for time_step in range(num_steps):
                if time_step > 0: tf.get_variable_scope().reuse_variables()
                cell_output, state = cell(inputs[:, time_step, :], state)
                outputs.append(cell_output) 
        # 把输出队列展开成[batch, hidden_size*num_steps]的形状，然后再
        # reshape成[batch*numsteps, hidden_size]的形状。
        output = tf.reshape(tf.concat(outputs, 1), [-1, HIDDEN_SIZE])
 
        # Softmax层：将RNN在每个位置上的输出转化为各个单词的logits。
        if SHARE_EMB_AND_SOFTMAX:
            weight = tf.transpose(embedding)
        else:
            weight = tf.get_variable("weight", [HIDDEN_SIZE, VOCAB_SIZE])
        bias = tf.get_variable("bias", [VOCAB_SIZE])
        logits = tf.matmul(output, weight) + bias
        
        # 定义交叉熵损失函数和平均损失。
        loss = tf.nn.sparse_softmax_cross_entropy_with_logits(
            labels=tf.reshape(self.targets, [-1]),
            logits=logits)
        self.cost = tf.reduce_sum(loss) / batch_size
        self.final_state = state
        
        # 只在训练模型时定义反向传播操作。
        if not is_training: return

        trainable_variables = tf.trainable_variables()
        # 控制梯度大小，定义优化方法和训练步骤。
        grads, _ = tf.clip_by_global_norm(
            tf.gradients(self.cost, trainable_variables), MAX_GRAD_NORM)
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=1.0)
        self.train_op = optimizer.apply_gradients(
            zip(grads, trainable_variables))


3.定义数据和训练过程。

In [4]:
# 使用给定的模型model在数据data上运行train_op并返回在全部数据上的perplexity值。
def run_epoch(session, model, batches, train_op, output_log, step):
    # 计算平均perplexity的辅助变量。
    total_costs = 0.0
    iters = 0
    state = session.run(model.initial_state) 
    # 训练一个epoch。
    for x, y in batches:
        # 在当前batch上运行train_op并计算损失值。交叉熵损失函数计算的就是下一个单
        # 词为给定单词的概率。
        cost, state, _ = session.run(
             [model.cost, model.final_state, train_op],
             {model.input_data: x, model.targets: y,
              model.initial_state: state})
        total_costs += cost
        iters += model.num_steps

        # 只有在训练时输出日志。
        if output_log and step % 100 == 0:
            print("After %d steps, perplexity is %.3f" % (
                  step, np.exp(total_costs / iters)))
        step += 1

    # 返回给定模型在给定数据上的perplexity值。
    return step, np.exp(total_costs / iters)


# 从文件中读取数据，并返回包含单词编号的数组。
def read_data(file_path):
    with open(file_path, "r") as fin:
        # 将整个文档读进一个长字符串。
        id_string = ' '.join([line.strip() for line in fin.readlines()])
    id_list = [int(w) for w in id_string.split()]  # 将读取的单词编号转为整数
    return id_list

def make_batches(id_list, batch_size, num_step):
    # 计算总的batch数量。每一个batch包含的单词数量是batch_sieze * num_step
    num_batches = (len(id_list) - 1) // (batch_size * num_step)
    
    # 将数据整理成一个维度为[batch_size, num_batches * num_step]的二维数组
    data = np.array(id_list[: num_batches * batch_size * num_step])
    data = np.reshape(data, [batch_size, num_batches * num_step])
    # 沿着第二个维度将数据切分成num_batches个batch，存入一个数组
    data_batches = np.split(data, num_batches, axis = 1)
    
    # 重复上一个操作，这里得到的是RNN每一步输出所需要预测的下一个单词
    label = np.array(id_list[1 : num_batches * batch_size * num_step + 1])
    label = np.reshape(label, [batch_size, num_batches * num_step])
    label_batches = np.split(label, num_batches, axis = 1)
    
    # 返回一个长度为num_batches的数组，每一项包括一个data矩阵和一个label矩阵
    return list(zip(data_batches, label_batches))

4.获得ptb文件

In [5]:
import codecs
import collections
from operator import itemgetter
import sys

def get_id(word,word_to_id):


    # 如果发现了被删除的低频词，则替换为"<unk>
    
    return word_to_id[word] if word in word_to_id else word_to_id["<unk>"]

def get_vocab(RAW_DATA):
    # RAW_DATA = "C:/Users/gdtop/Desktop/simple-examples/data/ptb.train.txt"
    VOCAB_OUTPUT = 'ptb.vocab'            # 输出词汇表文件

    counter = collections.Counter()       # 统计单词出现频率count
    with codecs.open(RAW_DATA, "r", "utf-8") as f:  # 每一行读取
        for line in f:
            for word in line.strip().split():       # 切割分词
                counter[word] += 1

    # 按照词频顺序对单词排序
    sorted_word_to_cnt = sorted(counter.items(),
                               key = itemgetter(1),
                               reverse = True)
    sorted_words = [x[0] for x in sorted_word_to_cnt]

    # 在文本换行处加上句子结束符<eos>，预先加入词汇表
    sorted_words = ["<eos>"] + sorted_words

    '''
    除了<eos>还需要将低频<unk>和句子起始符<sos>加入词汇表，并且删除低频词汇，因为在PTB数据中已经替换了低频词汇，所以不需要这一步
    sorted_words = ["<unk>","<sos>","<eos>"] + sorted_words
    if len(sorted_words)>10000:
    sorted_words = sorted_words[:10000]
    '''
    with codecs.open(VOCAB_OUTPUT, 'w', 'utf-8') as file_output:
        for word in sorted_words:
            file_output.write(word + "\n")
        #print("success")
    
    return VOCAB_OUTPUT
        
    # OUTPUT_DATA = "ptb.train"                 # 将单词替换问单词编号后的输出文件

def ptb_write(RAW_DATA,OUTPUT_DATA,VOCAB_OUTPUT):
    
    # 读取词汇表，并建立词汇到单词编号的映射
    with codecs.open(VOCAB_OUTPUT, 'r', 'utf-8') as f_vocab:
        vocab = [w.strip() for w in f_vocab.readlines()]
    word_to_id = {k: v for (k, v) in zip(vocab, range(len(vocab)))}
    
    fin = codecs.open(RAW_DATA, "r", "utf-8")
    fout = codecs.open(OUTPUT_DATA, "w", "utf-8")
    for line in fin: 
        words = line.strip().split() + ["<eos>"] # 读取单词并添加<eos>结束符
        # 将每个单词替换为词汇表的编号
        out_line = ' '.join([str(get_id(w,word_to_id)) for w in words]) + '\n'
        fout.write(out_line)
        #print(out_line)
    fin.close()
    fout.close()

def get_ptb(RAW_DATA, OUTPUT_DATA):
    VOCAB_OUTPUT = get_vocab(RAW_DATA)
    ptb_write(RAW_DATA,OUTPUT_DATA,VOCAB_OUTPUT)

5. 主函数。

In [ ]:
def main():
    # 定义初始化函数。
    initializer = tf.random_uniform_initializer(-0.05, 0.05)
    
    # 定义训练用的循环神经网络模型。
    with tf.variable_scope("language_model", 
                           reuse=None, initializer=initializer):
        train_model = PTBModel(True, TRAIN_BATCH_SIZE, TRAIN_NUM_STEP)

    # 定义测试用的循环神经网络模型。它与train_model共用参数，但是没有dropout。
    with tf.variable_scope("language_model",
                           reuse=True, initializer=initializer):
        eval_model = PTBModel(False, EVAL_BATCH_SIZE, EVAL_NUM_STEP)
    # 获得ptb文件
    #get_ptb(TRAIN_PATH, TRAIN_DATA)
    #get_ptb(EVAL_PATH, EVAL_DATA)
    #get_ptb(TEST_PATH, TEST_DATA)
    # 训练模型。
    with tf.Session() as session:
        tf.global_variables_initializer().run()
        train_batches = make_batches(
            read_data(TRAIN_DATA), TRAIN_BATCH_SIZE, TRAIN_NUM_STEP)
        eval_batches = make_batches(
            read_data(EVAL_DATA), EVAL_BATCH_SIZE, EVAL_NUM_STEP)
        test_batches = make_batches(
            read_data(TEST_DATA), EVAL_BATCH_SIZE, EVAL_NUM_STEP)

        step = 0
        for i in range(NUM_EPOCH):
            print("In iteration: %d" % (i + 1))
            step, train_pplx = run_epoch(session, train_model, train_batches,
                                         train_model.train_op, True, step)
            print("Epoch: %d Train Perplexity: %.3f" % (i + 1, train_pplx))

            _, eval_pplx = run_epoch(session, eval_model, eval_batches,
                                     tf.no_op(), False, 0)
            print("Epoch: %d Eval Perplexity: %.3f" % (i + 1, eval_pplx))

        _, test_pplx = run_epoch(session, eval_model, test_batches,
                                 tf.no_op(), False, 0)
        print("Test Perplexity: %.3f" % test_pplx)

if __name__ == "__main__":
    main()

In iteration: 1
After 0 steps, perplexity is 10073.931
After 100 steps, perplexity is 1744.006
After 200 steps, perplexity is 1168.841
After 300 steps, perplexity is 916.193
After 400 steps, perplexity is 750.564
After 500 steps, perplexity is 639.868
After 600 steps, perplexity is 566.440
After 700 steps, perplexity is 509.976
After 800 steps, perplexity is 460.748
After 900 steps, perplexity is 424.360
After 1000 steps, perplexity is 398.052
After 1100 steps, perplexity is 371.604
After 1200 steps, perplexity is 350.897
After 1300 steps, perplexity is 330.978
Epoch: 1 Train Perplexity: 327.840
Epoch: 1 Eval Perplexity: 186.091
In iteration: 2
After 1400 steps, perplexity is 179.818
After 1500 steps, perplexity is 165.154
After 1600 steps, perplexity is 167.478
After 1700 steps, perplexity is 164.945
After 1800 steps, perplexity is 160.354
After 1900 steps, perplexity is 158.259
After 2000 steps, perplexity is 156.746
After 2100 steps, perplexity is 152.110
After 2200 steps, perplexit

In [ ]:
def main():
    # 定义初始化函数。
    initializer = tf.random_uniform_initializer(-0.05, 0.05)
    
    # 定义训练用的循环神经网络模型。
    with tf.variable_scope("language_model", 
                           reuse=None, initializer=initializer):
        train_model = PTBModel(True, TRAIN_BATCH_SIZE, TRAIN_NUM_STEP)

    # 定义测试用的循环神经网络模型。它与train_model共用参数，但是没有dropout。
    with tf.variable_scope("language_model",
                           reuse=True, initializer=initializer):
        eval_model = PTBModel(False, EVAL_BATCH_SIZE, EVAL_NUM_STEP)
    # 获得ptb文件
    get_ptb(TRAIN_PATH, TRAIN_DATA)
    get_ptb(EVAL_PATH, EVAL_DATA)
    get_ptb(TEST_PATH, TEST_DATA)
    # 训练模型。
    with tf.Session() as session:
        tf.global_variables_initializer().run()
        train_batches = make_batches(
            read_data(TRAIN_DATA), TRAIN_BATCH_SIZE, TRAIN_NUM_STEP)
        eval_batches = make_batches(
            read_data(EVAL_DATA), EVAL_BATCH_SIZE, EVAL_NUM_STEP)
        test_batches = make_batches(
            read_data(TEST_DATA), EVAL_BATCH_SIZE, EVAL_NUM_STEP)

        step = 0
        for i in range(NUM_EPOCH):
            print("In iteration: %d" % (i + 1))
            step, train_pplx = run_epoch(session, train_model, train_batches,
                                         train_model.train_op, True, step)
            print("Epoch: %d Train Perplexity: %.3f" % (i + 1, train_pplx))

            _, eval_pplx = run_epoch(session, eval_model, eval_batches,
                                     tf.no_op(), False, 0)
            print("Epoch: %d Eval Perplexity: %.3f" % (i + 1, eval_pplx))

        _, test_pplx = run_epoch(session, eval_model, test_batches,
                                 tf.no_op(), False, 0)
        print("Test Perplexity: %.3f" % test_pplx)

if __name__ == "__main__":
    main()

In iteration: 1
After 0 steps, perplexity is 10017.286
After 100 steps, perplexity is 1832.468
After 200 steps, perplexity is 1176.753
After 300 steps, perplexity is 909.458
After 400 steps, perplexity is 740.021
After 500 steps, perplexity is 628.158
After 600 steps, perplexity is 555.553
After 700 steps, perplexity is 500.116
After 800 steps, perplexity is 451.754
After 900 steps, perplexity is 416.070
After 1000 steps, perplexity is 390.382
After 1100 steps, perplexity is 364.529
After 1200 steps, perplexity is 344.242
After 1300 steps, perplexity is 324.843
Epoch: 1 Train Perplexity: 321.768
Epoch: 1 Eval Perplexity: 1527.050
In iteration: 2
After 1400 steps, perplexity is 176.981
After 1500 steps, perplexity is 163.254
After 1600 steps, perplexity is 165.402
After 1700 steps, perplexity is 162.333
After 1800 steps, perplexity is 157.729
After 1900 steps, perplexity is 155.631
After 2000 steps, perplexity is 154.035
After 2100 steps, perplexity is 149.376
After 2200 steps, perplexi

In [ ]:
import codecs
import collections
from operator import itemgetter
import sys

# 1. 设置参数。
MODE = "PTB"    # 将MODE设置为"PTB", "TRANSLATE_EN", "TRANSLATE_ZH"之一。

if MODE == "PTB":             # PTB数据处理
    RAW_DATA = "../../datasets/PTB_data/ptb.train.txt"  # 训练集数据文件
    VOCAB_OUTPUT = "ptb.vocab"                         # 输出的词汇表文件
elif MODE == "TRANSLATE_ZH":  # 翻译语料的中文部分
    RAW_DATA = "../../datasets/TED_data/train.txt.zh"
    VOCAB_OUTPUT = "zh.vocab"
    VOCAB_SIZE = 4000
elif MODE == "TRANSLATE_EN":  # 翻译语料的英文部分
    RAW_DATA = "../../datasets/TED_data/train.txt.en"
    VOCAB_OUTPUT = "en.vocab"
    VOCAB_SIZE = 10000
    
# 2.对单词按词频排序。
counter = collections.Counter()
with codecs.open(RAW_DATA, "r", "utf-8") as f:
    for line in f:
        for word in line.strip().split():
            counter[word] += 1

# 按词频顺序对单词进行排序。
sorted_word_to_cnt = sorted(
    counter.items(), key=itemgetter(1), reverse=True)
sorted_words = [x[0] for x in sorted_word_to_cnt]

# 3.插入特殊符号。
if MODE == "PTB":
    # 稍后我们需要在文本换行处加入句子结束符"<eos>"，这里预先将其加入词汇表。
    sorted_words = ["<eos>"] + sorted_words
elif MODE in ["TRANSLATE_EN", "TRANSLATE_ZH"]:
    # 在9.3.2小节处理机器翻译数据时，除了"<eos>"以外，还需要将"<unk>"和句子起始符
    # "<sos>"加入词汇表，并从词汇表中删除低频词汇。
    sorted_words = ["<unk>", "<sos>", "<eos>"] + sorted_words
    if len(sorted_words) > VOCAB_SIZE:
        sorted_words = sorted_words[:VOCAB_SIZE]

# 4.保存词汇表文件。
with codecs.open(VOCAB_OUTPUT, 'w', 'utf-8') as file_output:
    for word in sorted_words:
        file_output.write(word + "\n")

# 1. 参数设置。
MODE = "PTB_TRAIN"    # 将MODE设置为"PTB_TRAIN", "PTB_VALID", "PTB_TEST", "TRANSLATE_EN", "TRANSLATE_ZH"之一。

if MODE == "PTB_TRAIN":        # PTB训练数据
    RAW_DATA = "../../datasets/PTB_data/ptb.train.txt"  # 训练集数据文件
    VOCAB = "ptb.vocab"                                 # 词汇表文件
    OUTPUT_DATA = "ptb.train"                           # 将单词替换为单词编号后的输出文件
elif MODE == "PTB_VALID":      # PTB验证数据
    RAW_DATA = "../../datasets/PTB_data/ptb.valid.txt"
    VOCAB = "ptb.vocab"
    OUTPUT_DATA = "ptb.valid"
elif MODE == "PTB_TEST":       # PTB测试数据
    RAW_DATA = "../../datasets/PTB_data/ptb.test.txt"
    VOCAB = "ptb.vocab"
    OUTPUT_DATA = "ptb.test"
elif MODE == "TRANSLATE_ZH":   # 中文翻译数据
    RAW_DATA = "../../datasets/TED_data/train.txt.zh"
    VOCAB = "zh.vocab"
    OUTPUT_DATA = "train.zh"
elif MODE == "TRANSLATE_EN":   # 英文翻译数据
    RAW_DATA = "../../datasets/TED_data/train.txt.en"
    VOCAB = "en.vocab"
    OUTPUT_DATA = "train.en"
    
# 2.按词汇表对将单词映射到编号。
# 读取词汇表，并建立词汇到单词编号的映射。
with codecs.open(VOCAB, "r", "utf-8") as f_vocab:
    vocab = [w.strip() for w in f_vocab.readlines()]
word_to_id = {k: v for (k, v) in zip(vocab, range(len(vocab)))}

# 如果出现了不在词汇表内的低频词，则替换为"unk"。
def get_id(word):
    return word_to_id[word] if word in word_to_id else word_to_id["<unk>"]

# 3.对数据进行替换并保存结果。
fin = codecs.open(RAW_DATA, "r", "utf-8")
fout = codecs.open(OUTPUT_DATA, 'w', 'utf-8')
for line in fin:
    words = line.strip().split() + ["<eos>"]  # 读取单词并添加<eos>结束符
    # 将每个单词替换为词汇表中的编号
    out_line = ' '.join([str(get_id(w)) for w in words]) + '\n'
    fout.write(out_line)
fin.close()
fout.close()


## 9.3 神经网络机器翻译
最基础的机器翻译算法——Seq2Seq模型，介绍机器翻译的数据集以及数据预处理方法，而且还有一个s2s的重要改进——注意力机制（attention）。

### 9.3.1 机器翻译背景与Seq2Seq模型介绍
       模型的训练步骤可分为预处理、词对齐、短语对齐、抽取短语特征（feature）、训练语言模型、学习特征权重。Seq2Seq模型的基本思想——使用一个循环神经网络读取这个编码，将其解压为目标语言的一个句子。这两个循环神经网络分别称为编码器（Encoder）和解码器（Decoder）。



       对于seq2seq的decoder，它在训练阶段和预测阶段对rnn的输出的处理可能是不一样的，比如在训练阶段可能对rnn的输出不处理，直接用target的序列作为下时刻的输入，如上图一。而预测阶段会将rnn的输出当成是下一时刻的输入，因为此时已经没有target序列可以作为输入了，如上图二。

       解码器结构与语言模型基本相同：输入为单词的词向量，输出为softmax产生的单词概率，损失函数为log perplexity。解码器的第一个输入时一个特殊的输入<sos>(Start-Of-Sentence)字符，每一步预测的单词时训练数据的目标句子，预测序列的结尾是<eos>字符。



### 9.3.2 机器翻译文本数据的预处理
机器翻译领域重要数据集是WMT数据集，选取中英的图标下载数据。下面以中英翻译为例，数据集包含21万个句子对，内容是TED演讲字幕。

In [1]:
# perl moses_tokenizer.perl -no-escape -l en < ./train.raw.en> train.txt.en

1.参数设置。

In [1]:
import tensorflow as tf

# 假设输入数据已经用9.2.1小节中的方法转换成了单词编号的格式。
SRC_TRAIN_DATA = "C:/Users/adward/Desktop/TensorFlow-Google/train.en"        # 源语言输入文件。
TRG_TRAIN_DATA = "C:/Users/adward/Desktop/TensorFlow-Google/train.zh"        # 目标语言输入文件。
CHECKPOINT_PATH = "C:/Users/adward/Desktop/TensorFlow-Google/seq2seq_ckpt"   # checkpoint保存路径。  

HIDDEN_SIZE = 1024                   # LSTM的隐藏层规模。
NUM_LAYERS = 2                       # 深层循环神经网络中LSTM结构的层数。
SRC_VOCAB_SIZE = 10000               # 源语言词汇表大小。
TRG_VOCAB_SIZE = 4000                # 目标语言词汇表大小。
BATCH_SIZE = 100                     # 训练数据batch的大小。
NUM_EPOCH = 5                        # 使用训练数据的轮数。
KEEP_PROB = 0.8                      # 节点不被dropout的概率。
MAX_GRAD_NORM = 5                    # 用于控制梯度膨胀的梯度大小上限。
SHARE_EMB_AND_SOFTMAX = True         # 在Softmax层和词向量层之间共享参数。

MAX_LEN = 50   # 限定句子的最大单词数量。
SOS_ID  = 1    # 目标语言词汇表中<sos>的ID。

2.读取训练数据并创建Dataset。

In [2]:
# 使用Dataset从一个文件中读取一个语言的数据。
# 数据的格式为每行一句话，单词已经转化为单词编号。
def MakeDataset(file_path):
    dataset = tf.data.TextLineDataset(file_path)
    # 根据空格将单词编号切分开并放入一个一维向量。
    dataset = dataset.map(lambda string: tf.string_split([string]).values)
    # 将字符串形式的单词编号转化为整数。
    dataset = dataset.map(
        lambda string: tf.string_to_number(string, tf.int32))
    # 统计每个句子的单词数量，并与句子内容一起放入Dataset中。
    dataset = dataset.map(lambda x: (x, tf.size(x)))
    return dataset

# 从源语言文件src_path和目标语言文件trg_path中分别读取数据，并进行填充和
# batching操作。
def MakeSrcTrgDataset(src_path, trg_path, batch_size):
    # 首先分别读取源语言数据和目标语言数据。
    src_data = MakeDataset(src_path)
    trg_data = MakeDataset(trg_path)
    # 通过zip操作将两个Dataset合并为一个Dataset。现在每个Dataset中每一项数据ds
    # 由4个张量组成：
    #   ds[0][0]是源句子
    #   ds[0][1]是源句子长度
    #   ds[1][0]是目标句子
    #   ds[1][1]是目标句子长度
    dataset = tf.data.Dataset.zip((src_data, trg_data))

    # 删除内容为空（只包含<EOS>）的句子和长度过长的句子。
    def FilterLength(src_tuple, trg_tuple):
        ((src_input, src_len), (trg_label, trg_len)) = (src_tuple, trg_tuple)
        src_len_ok = tf.logical_and(
            tf.greater(src_len, 1), tf.less_equal(src_len, MAX_LEN))
        trg_len_ok = tf.logical_and(
            tf.greater(trg_len, 1), tf.less_equal(trg_len, MAX_LEN))
        return tf.logical_and(src_len_ok, trg_len_ok)
    dataset = dataset.filter(FilterLength)
    
    # 从图9-5可知，解码器需要两种格式的目标句子：
    #   1.解码器的输入(trg_input)，形式如同"<sos> X Y Z"
    #   2.解码器的目标输出(trg_label)，形式如同"X Y Z <eos>"
    # 上面从文件中读到的目标句子是"X Y Z <eos>"的形式，我们需要从中生成"<sos> X Y Z"
    # 形式并加入到Dataset中。
    def MakeTrgInput(src_tuple, trg_tuple):
        ((src_input, src_len), (trg_label, trg_len)) = (src_tuple, trg_tuple)
        trg_input = tf.concat([[SOS_ID], trg_label[:-1]], axis=0)
        return ((src_input, src_len), (trg_input, trg_label, trg_len))
    dataset = dataset.map(MakeTrgInput)

    # 随机打乱训练数据。
    dataset = dataset.shuffle(10000)

    # 规定填充后输出的数据维度。
    padded_shapes = (
        (tf.TensorShape([None]),      # 源句子是长度未知的向量
         tf.TensorShape([])),         # 源句子长度是单个数字
        (tf.TensorShape([None]),      # 目标句子（解码器输入）是长度未知的向量
         tf.TensorShape([None]),      # 目标句子（解码器目标输出）是长度未知的向量
         tf.TensorShape([])))         # 目标句子长度是单个数字
    # 调用padded_batch方法进行batching操作。
    batched_dataset = dataset.padded_batch(batch_size, padded_shapes)
    return batched_dataset

3.定义翻译模型。

In [3]:
# 定义NMTModel类来描述模型。
class NMTModel(object):
    # 在模型的初始化函数中定义模型要用到的变量。
    def __init__(self):
        # 定义编码器和解码器所使用的LSTM结构。
        self.enc_cell = tf.nn.rnn_cell.MultiRNNCell(
          [tf.nn.rnn_cell.BasicLSTMCell(HIDDEN_SIZE)
           for _ in range(NUM_LAYERS)])
        self.dec_cell = tf.nn.rnn_cell.MultiRNNCell(
          [tf.nn.rnn_cell.BasicLSTMCell(HIDDEN_SIZE) 
           for _ in range(NUM_LAYERS)])

        # 为源语言和目标语言分别定义词向量。   
        self.src_embedding = tf.get_variable(
            "src_emb", [SRC_VOCAB_SIZE, HIDDEN_SIZE])
        self.trg_embedding = tf.get_variable(
            "trg_emb", [TRG_VOCAB_SIZE, HIDDEN_SIZE])

        # 定义softmax层的变量
        if SHARE_EMB_AND_SOFTMAX:
           self.softmax_weight = tf.transpose(self.trg_embedding)
        else:
           self.softmax_weight = tf.get_variable(
               "weight", [HIDDEN_SIZE, TRG_VOCAB_SIZE])
        self.softmax_bias = tf.get_variable(
            "softmax_bias", [TRG_VOCAB_SIZE])

    # 在forward函数中定义模型的前向计算图。
    # src_input, src_size, trg_input, trg_label, trg_size分别是上面
    # MakeSrcTrgDataset函数产生的五种张量。
    def forward(self, src_input, src_size, trg_input, trg_label, trg_size):
        batch_size = tf.shape(src_input)[0]
    
        # 将输入和输出单词编号转为词向量。
        src_emb = tf.nn.embedding_lookup(self.src_embedding, src_input)
        trg_emb = tf.nn.embedding_lookup(self.trg_embedding, trg_input)
        
        # 在词向量上进行dropout。
        src_emb = tf.nn.dropout(src_emb, KEEP_PROB)
        trg_emb = tf.nn.dropout(trg_emb, KEEP_PROB)

        # 使用dynamic_rnn构造编码器。
        # 编码器读取源句子每个位置的词向量，输出最后一步的隐藏状态enc_state。
        # 因为编码器是一个双层LSTM，因此enc_state是一个包含两个LSTMStateTuple类
        # 张量的tuple，每个LSTMStateTuple对应编码器中的一层。
        # enc_outputs是顶层LSTM在每一步的输出，它的维度是[batch_size, 
        # max_time, HIDDEN_SIZE]。Seq2Seq模型中不需要用到enc_outputs，而
        # 后面介绍的attention模型会用到它。
        with tf.variable_scope("encoder"):
            enc_outputs, enc_state = tf.nn.dynamic_rnn(
                self.enc_cell, src_emb, src_size, dtype=tf.float32)

        # 使用dyanmic_rnn构造解码器。
        # 解码器读取目标句子每个位置的词向量，输出的dec_outputs为每一步
        # 顶层LSTM的输出。dec_outputs的维度是 [batch_size, max_time,
        # HIDDEN_SIZE]。
        # initial_state=enc_state表示用编码器的输出来初始化第一步的隐藏状态。
        with tf.variable_scope("decoder"):
            dec_outputs, _ = tf.nn.dynamic_rnn(
                self.dec_cell, trg_emb, trg_size, initial_state=enc_state)

        # 计算解码器每一步的log perplexity。这一步与语言模型代码相同。
        output = tf.reshape(dec_outputs, [-1, HIDDEN_SIZE])
        logits = tf.matmul(output, self.softmax_weight) + self.softmax_bias
        loss = tf.nn.sparse_softmax_cross_entropy_with_logits(
            labels=tf.reshape(trg_label, [-1]), logits=logits)

        # 在计算平均损失时，需要将填充位置的权重设置为0，以避免无效位置的预测干扰
        # 模型的训练。
        label_weights = tf.sequence_mask(
            trg_size, maxlen=tf.shape(trg_label)[1], dtype=tf.float32)
        label_weights = tf.reshape(label_weights, [-1])
        cost = tf.reduce_sum(loss * label_weights)
        cost_per_token = cost / tf.reduce_sum(label_weights)
        
        # 定义反向传播操作。反向操作的实现与语言模型代码相同。
        trainable_variables = tf.trainable_variables()

        # 控制梯度大小，定义优化方法和训练步骤。
        grads = tf.gradients(cost / tf.to_float(batch_size),
                             trainable_variables)
        grads, _ = tf.clip_by_global_norm(grads, MAX_GRAD_NORM)
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=1.0)
        train_op = optimizer.apply_gradients(
            zip(grads, trainable_variables))
        return cost_per_token, train_op

4.训练过程和主函数。

In [4]:
# 使用给定的模型model上训练一个epoch，并返回全局步数。
# 每训练200步便保存一个checkpoint。
def run_epoch(session, cost_op, train_op, saver, step):
    # 训练一个epoch。
    # 重复训练步骤直至遍历完Dataset中所有数据。
    while True:
        try:
            # 运行train_op并计算损失值。训练数据在main()函数中以Dataset方式提供。
            cost, _ = session.run([cost_op, train_op])
            if step % 10 == 0:
                print("After %d steps, per token cost is %.3f" % (step, cost))
            # 每200步保存一个checkpoint。
            if step % 200 == 0:
                saver.save(session, CHECKPOINT_PATH, global_step=step)
            step += 1
        except tf.errors.OutOfRangeError:
            break
    return step

def main():
    # 定义初始化函数。
    initializer = tf.random_uniform_initializer(-0.05, 0.05)

    # 定义训练用的循环神经网络模型。
    with tf.variable_scope("nmt_model", reuse=None, 
                           initializer=initializer):
        train_model = NMTModel()
  
    # 定义输入数据。
    data = MakeSrcTrgDataset(SRC_TRAIN_DATA, TRG_TRAIN_DATA, BATCH_SIZE)
    iterator = data.make_initializable_iterator()
    (src, src_size), (trg_input, trg_label, trg_size) = iterator.get_next()
 
    # 定义前向计算图。输入数据以张量形式提供给forward函数。
    cost_op, train_op = train_model.forward(src, src_size, trg_input,
                                            trg_label, trg_size)

    # 训练模型。
    saver = tf.train.Saver()
    step = 0
    with tf.Session() as sess:
        tf.global_variables_initializer().run()
        for i in range(NUM_EPOCH):
            print("In iteration: %d" % (i + 1))
            sess.run(iterator.initializer)
            step = run_epoch(sess, cost_op, train_op, saver, step)
if __name__ == "__main__":
    main()


AttributeError: module 'tensorflow' has no attribute 'data'

In [5]:
dataset = tf.data.TextLineDataset("C:/Users/adward/Desktop/TensorFlow-Google/train.en")
# 根据空格将单词编号切分开并放入一个一维向量。
dataset = dataset.map(lambda string: tf.string_split([string]).values)
# 将字符串形式的单词编号转化为整数。
dataset = dataset.map(
    lambda string: tf.string_to_number(string, tf.int32))
# 统计每个句子的单词数量，并与句子内容一起放入Dataset中。
dataset = dataset.map(lambda x: (x, tf.size(x)))

AttributeError: module 'tensorflow' has no attribute 'data'